Join all tables

In [0]:
from pyspark.sql.functions import *
from pyspark.sql.types import *

In [0]:
netflix_directors_gl_df = spark.read.format('delta').load("abfss://silver-ma@netflixdataengstorage.dfs.core.windows.net/netflix_directors")
netflix_cast_gl_df = spark.read.format('delta').load("abfss://silver-ma@netflixdataengstorage.dfs.core.windows.net/netflix_cast")
netflix_category_gl_df = spark.read.format('delta').load("abfss://silver-ma@netflixdataengstorage.dfs.core.windows.net/netflix_category")
netflix_titles_gl_df = spark.read.format('delta').load("abfss://silver-ma@netflixdataengstorage.dfs.core.windows.net/netflix_titles")
netflix_countries_gl_df = spark.read.format('delta').load("abfss://silver-ma@netflixdataengstorage.dfs.core.windows.net/netflix_countries")

gold_layer_joins_df = netflix_titles_gl_df.join(netflix_cast_gl_df, "show_id", "left")\
.join(netflix_directors_gl_df, "show_id", "left")\
.join(netflix_category_gl_df, "show_id", "left")\
.join(netflix_countries_gl_df, "show_id", "left")


**Drop null columns**

In [0]:
gold_layer_joins_df = gold_layer_joins_df.drop("_rescued_data", "duration_ranking")

**Converting the normalized data into denormalized data to perform Analytics for dashboard**

In [0]:
gold_layer_joins_df_final = (
    gold_layer_joins_df.groupBy(
         "show_id",
         "duration_minutes",
         "duration_seasons",
         "type",
         "title",
         "date_added",
         "release_year",
         "rating",
         "description",
         "ShortTitle",
         "type_flag"
      )
      .agg(
         concat_ws(", ", collect_set("cast")).alias("cast"),
         concat_ws(", ", collect_set("listed_in")).alias("categories"),
         concat_ws(", ", collect_set("director")).alias("director"),
         concat_ws(", ", collect_set("country")).alias("country")
      )
)

In [0]:
random_5_digit = (expr("floor(rand() * 90000) + 10000"))
gold_layer_joins_df_final = gold_layer_joins_df_final.withColumn(
    "show_id",
    when(col("show_id").isNull(), random_5_digit).otherwise(col("show_id"))
)
gold_layer_joins_df_final = gold_layer_joins_df_final.withColumn(
    "release_year",
    col("release_year").cast(IntegerType())
).orderBy(col("release_year").desc())

In [0]:
gold_layer_joins_df_final = gold_layer_joins_df_final.withColumn("cast", coalesce(col("cast"), lit("Unknown")))\
                                                     .withColumn("categories", coalesce(col("categories"), lit("Unknown")))\
                                                     .withColumn("director", coalesce(col("director"), lit("Unknown")))\
                                                     .withColumn("country", coalesce(col("country"), lit("Unknown")))
display(gold_layer_joins_df_final)

show_id duration_minutes duration_seasons type title date_added release_year rating description ShortTitle type_flag cast categories director country 80996973 0 1 TV Show Handsome Siblings 1/16/2020 2020 TV-14 Clashing martial arts twins face relentless villains, thorny romance and brotherly rivalry as their troubled pasts catch up to them. Handsome Siblings 2 Hu Yitian, Gallen Lo, Nikita Mao, Jason Zheng, Tay Ping Hui, Liang Jie, Vicky Liang, Chen Zheyuan, Jin Song, Song Wenzuo TV Dramas, TV Sci-Fi & Fantasy, International TV Shows China 80233408 102 1 Movie Live Twice, Love Once 1/7/2020 2020 TV-MA When Emilio (Oscar Martínez) is diagnosed with Alzheimer's disease, he and his family embark on a quest to reunite him with his childhood crush. Live Twice, Love Once 1 Hugo Balaguer, Mafalda Carbonell, Aina Clotet, María Zamora, Oscar Martínez, Valeria Schoneveld, Inma Cuesta, Antonio Valero, Nacho López, Isabel Requena International Movies, Dramas, Comedies Maria Ripoll Spain 80221553 0 1 TV Show Kipo and the Age of Wonderbeasts 1/14/2020 2020 TV-Y7-FV Making her way through a world of mutant animals, a sheltered yet scrappy girl learns how to survive – and get home – with help from her ragtag crew. Kipo and the Age of Wonderbeasts 2 Coy Stewart, Dan Stevens, Jake Green, Sydney Mikayla, Deon Cole, Sterling K. Brown, Steve Blum, Karen Fukuhara, Dee Bradley Baker TV Comedies, Kids' TV United States 80237347 0 1 TV Show Go! Go! Cory Carson 1/4/2020 2020 TV-Y Beep, beep – go, go! Buckle up for fun and adventure with adorable kid car Cory Carson as he explores the winding roads of Bumperton Hills. Go! Go! Cory Carson 2 Anna Chambers, Maisie Benson, Pfifer Chastain, Adelaide Hirasaki, Alan C. Lim, Kerry Gudjohnsen, Smith Foreman, Neena-Sinaii Simpo, Jim Capobianco, Eli Morse, Paul Killam Kids' TV United States 80117557 0 1 TV Show Messiah 1/1/2020 2020 TV-MA A wary CIA officer investigates a charismatic man who sparks a spiritual movement and stirs political unrest. A fictional story not based on true events. Messiah 2 Michelle Monaghan, John Ortiz, Melinda Page Hamilton, Stefania LaVie Owen, Jane Adams, Sayyid El Alami, Mehdi Dehbi, Fares Landoulsi, Tomer Sisley, Wil Traval TV Dramas, TV Thrillers United States 81127902 121 1 Movie A Fall from Grace 1/17/2020 2020 TV-MA When gentle, law-abiding Grace confesses to killing her new husband, her skeptical young lawyer sets out to uncover the truth. A film by Tyler Perry. A Fall from Grace 1 Cicely Tyson, Phylicia Rashad, Tyler Perry, Mehcad Brooks, Bresha Webb, Adrian Pasdar, Crystal Fox Dramas, Thrillers Tyler Perry 81006825 90 1 Movie All the Freckles in the World 1/3/2020 2020 TV-14 Thirteen-year-old José Miguel is immune to 1994 World Cup fever until he realizes soccer is the only way to win the heart of his crush. All the Freckles in the World 1 Juan Carlos Viana Prieto, Loreto Peralta, Daniel Haddad, Hánssel Casillas, Montserrat Marañón, Hernán Del Riego, Alejandro Flores, Luis De La Rosa, Andrea Sutton, Anajosé Aldrete International Movies, Comedies, Romantic Movies Yibrán Asuad Mexico 80197991 0 1 TV Show Nisman: The Prosecutor, the President, and the Spy 1/1/2020 2020 TV-MA This docuseries details the suspicious death of Alberto Nisman, investigator of the 1994 bombing of the Argentine Israelite Mutual Association building. Nisman 2 Crime TV Shows, International TV Shows, Docuseries Justin Webster 81183491 0 1 TV Show Jamtara - Sabka Number Ayega 1/10/2020 2020 TV-MA A group of small-town young men run a lucrative phishing operation, until a corrupt politician wants in on their scheme – and a cop wants to fight it. Jamtara - Sabka Number Ayega 2 Dibyendu Bhattacharya, Aksha Pardhasany, Amit Sial, Sparsh Shrivastava, Monika Panwar, Anshumaan Pushkar Crime TV Shows, TV Dramas, International TV Shows Soumendra Padhi India 80239306 0 1 TV Show The Healing Powers of Dude 1/13/2020 2020 TV-G When an 11-year-old boy with social anxiety disorder starts middle school, he finds strength i

In [0]:
# save inside gold layer as netflix-analytics
gold_layer_joins_df_final.write.format('csv')\
                    .mode('overwrite')\
                    .option("path", "abfss://gold-ma@netflixdataengstorage.dfs.core.windows.net/netflix_analytics-prod")\
                    .save()